In [68]:
from matplotlib import pyplot as plt
import numpy as np
from scipy import signal as sig
import struct
import random
import ipywidgets
import itertools
from multiprocessing import Pool

import colorednoise

np.set_printoptions(linewidth=240)

In [3]:
%matplotlib widget

In [4]:
sampling_rate = 10 # sp/s

In [59]:
# From https://github.com/mubeta06/python/blob/master/signal_processing/sp/gold.py
preferred_pairs = {5:[[2],[1,2,3]], 6:[[5],[1,4,5]], 7:[[4],[4,5,6]],
                        8:[[1,2,3,6,7],[1,2,7]], 9:[[5],[3,5,6]], 
                        10:[[2,5,9],[3,4,6,8,9]], 11:[[9],[3,6,9]]}

def gen_gold(seq1, seq2):
    gold = [seq1, seq2]
    for shift in range(len(seq1)):
        gold.append(seq1 ^ np.roll(seq2, -shift))
    return gold

def gold(n):
    n = int(n)
    if not n in preferred_pairs:
        raise KeyError('preferred pairs for %s bits unknown' % str(n))
    t0, t1 = preferred_pairs[n]
    (seq0, _st0), (seq1, _st1) = sig.max_len_seq(n, taps=t0), sig.max_len_seq(n, taps=t1)
    return gen_gold(seq0, seq1)

In [6]:
def modulate(data, nbits=5):
    # 0, 1 -> -1, 1
    mask = np.array(gold(nbits))*2 - 1
    
    sel = mask[data>>1]
    data_lsb_centered = ((data&1)*2 - 1)

    return (np.multiply(sel, np.tile(data_lsb_centered, (2**nbits-1, 1)).T).flatten() + 1) // 2

In [7]:
def correlate(sequence, nbits=5, decimation=1, mask_filter=lambda x: x):
    mask = np.tile(np.array(gold(nbits))[:,:,np.newaxis]*2 - 1, (1, 1, decimation)).reshape((2**nbits + 1, (2**nbits-1) * decimation))

    sequence -= np.mean(sequence)
    
    return np.array([np.correlate(sequence, row, mode='full') for row in mask])

In [8]:
with open('/mnt/c/Users/jaseg/shared/raw_freq.bin', 'rb') as f:
    mains_noise = np.copy(np.frombuffer(f.read(), dtype='float32'))
    print('mean:', np.mean(mains_noise))
    mains_noise -= np.mean(mains_noise)

mean: 49.98625


In [72]:
def generate_test_signal(duration, nbits=6, signal_amplitude=2.0e-3, decimation=10, seed=0):
    test_data = np.random.RandomState(seed=seed).randint(0, 2 * (2**nbits), duration)
    
    signal = np.repeat(modulate(test_data, nbits) * 2.0 - 1, decimation) * signal_amplitude
    noise = np.resize(mains_noise, len(signal))
    
    return test_data, signal + noise

In [10]:
nonlinear_distance = lambda x: 100**(2*np.abs(0.5-x%1)) / (np.abs(x)+3)**2

def plot_distance_func():
    fig, ax = plt.subplots()
    x = np.linspace(-1.5, 5.5, 10000)
    ax.plot(x, nonlinear_distance(x))

In [38]:
noprint = lambda *args, **kwargs: None

In [74]:
def run_ser_test(sample_duration=128, nbits=6, signal_amplitude=2.0e-3, decimation=10, threshold_factor=4.0, power_avg_width=2.5, max_lookahead=6.5, seed=0, ax=None, print=print):

    test_data, signal = generate_test_signal(sample_duration, nbits, signal_amplitude, decimation, seed)
    cor_an = correlate(signal, nbits=nbits, decimation=decimation)

    power_avg_width = int(power_avg_width * (2**nbits - 1) * decimation)

    bit_period = (2**nbits) * decimation
    peak_group_threshold = 0.1 * bit_period
    
    cwt_res = np.array([ sig.cwt(row, sig.ricker, [0.73 * decimation]).flatten() for row in cor_an ])
    if ax:
        ax.grid()
        ax.plot(cwt_res.T)
        
    th = np.array([ np.convolve(np.abs(row), np.ones((power_avg_width,))/power_avg_width, mode='same') for row in cwt_res ])

    def compare_th(elem):
        idx, (th, val) = elem
        #print('compare_th:', th.shape, val.shape)
        return np.any(np.abs(val) > th*threshold_factor)

    peaks = [ list(group) for val, group in itertools.groupby(enumerate(zip(th.T, cwt_res.T)), compare_th) if val ]
    peak_group = []
    for group in peaks:
        pos = np.mean([idx for idx, _val in group])
        pol = np.mean([max(val.min(), val.max(), key=abs) for _idx, (_th, val) in group])
        pol_idx = np.argmax(np.bincount([ np.argmax(np.abs(val)) for _idx, (_th, val) in group ]))
        #print(f'group', pos, pol, pol_idx)
        #for pol, (_idx, (_th, val)) in zip([max(val.min(), val.max(), key=abs) for _idx, (_th, val) in group], group):
        #    print('    ', pol, val)
        if ax:
            ax.axvline(pos, color='cyan', alpha=0.3)

        if not peak_group or pos - peak_group[-1][1] > peak_group_threshold:
            if peak_group:
                peak_pos = peak_group[-1][3]
                if ax:
                    ax.axvline(peak_pos, color='red', alpha=0.6)
                #ax3.text(peak_pos-20, 2.0, f'{0 if pol < 0 else 1}', horizontalalignment='right', verticalalignment='center', color='black')

            peak_group.append((pos, pos, pol, pos, pol_idx))
            #ax3.axvline(pos, color='cyan', alpha=0.5)

        else:
            group_start, last_pos, last_pol, peak_pos, last_pol_idx = peak_group[-1]

            if abs(pol) > abs(last_pol):
                #ax3.axvline(pos, color='magenta', alpha=0.5)
                peak_group[-1] = (group_start, pos, pol, pos, pol_idx)
            else:
                #ax3.axvline(pos, color='blue', alpha=0.5)
                peak_group[-1] = (group_start, pos, last_pol, peak_pos, last_pol_idx)

    avg_peak = np.mean(np.abs(np.array([last_pol for _1, _2, last_pol, _3, _4 in peak_group])))
    print('avg_peak', avg_peak)

    noprint = lambda *args, **kwargs: None
    def mle_decode(peak_groups, print=print):
        peak_groups = [ (pos, pol, idx) for _1, _2, pol, pos, idx in peak_groups ]
        candidates = [ (0, [(pos, pol, idx)]) for pos, pol, idx in peak_groups if pos < bit_period*2.5 ]

        while candidates:
            chain_candidates = []
            for chain_score, chain in candidates:
                pos, ampl, _idx = chain[-1]
                score_fun = lambda pos, npos, npol: abs(npol)/avg_peak + nonlinear_distance((npos-pos)/bit_period)
                next_candidates = sorted([ (score_fun(pos, npos, npol), npos, npol, nidx) for npos, npol, nidx in peak_groups if pos < npos < pos + bit_period*max_lookahead ], reverse=True)

                print(f'    candidates for {pos}, {ampl}:')
                for score, npos, npol, nidx in next_candidates:
                    print(f'        {score:.4f} {npos:.2f} {npol:.2f} {nidx:.2f}')

                nch, cor_len = cor_an.shape
                if cor_len - pos < 1.5*bit_period or not next_candidates:
                    score = sum(score_fun(opos, npos, npol) for (opos, _opol, _oidx), (npos, npol, _nidx) in zip(chain[:-1], chain[1:])) / len(chain)
                    yield score, chain

                else:
                    print('extending')
                    for score, npos, npol, nidx in next_candidates[:3]:
                        if score > 0.5:
                            new_chain_score = chain_score * 0.9 + score * 0.1
                            chain_candidates.append((new_chain_score, chain + [(npos, npol, nidx)]))
            print('chain candidates:')
            for score, chain in sorted(chain_candidates, reverse=True):
                print('    ', [(score, [(f'{pos:.2f}', f'{pol:.2f}') for pos, pol, _idx in chain])])
            candidates = [ (chain_score, chain) for chain_score, chain in sorted(chain_candidates, reverse=True)[:10] ]

    res = sorted(mle_decode(peak_group, print=noprint), reverse=True)
    #for i, (score, chain) in enumerate(res):
    #    print(f'Chain {i}@{score:.4f}: {chain}')
    (_score, chain), *_ = res

    def viz(chain):
        last_pos = None
        for pos, pol, nidx in chain:
            if last_pos:
                delta = int(round((pos - last_pos) / bit_period))
                if delta > 1:
                    print(f'skipped {delta} symbols at {pos}')
                for i in range(delta-1):
                    yield None
            decoded = nidx*2 + (0 if pol < 0 else 1)
            yield decoded
            if ax:
                ax.axvline(pos, color='blue', alpha=0.5)
                ax.text(pos-20, 0.0, f'{decoded}', horizontalalignment='right', verticalalignment='center', color='black')

            last_pos = pos

    decoded = list(viz(chain))
    print('decoding [ref|dec]:')
    failures = 0
    for i, (ref, found) in enumerate(itertools.zip_longest(test_data, decoded)):
        print(f'{ref or -1:>3d}|{found or -1:>3d} {"✔" if ref==found else "✘" if found else " "}', end='    ')
        if ref != found:
            failures += 1
        if i%8 == 7:
            print()
    ser = failures/len(test_data)
    print(f'Symbol error rate e={ser}')
    br = sampling_rate / decimation / (2**nbits) * nbits * (1 - ser) * 3600
    print(f'maximum bitrate r={br} b/h')
    return ser, br

In [39]:
fig, ax = plt.subplots(figsize=(12,5))
run_ser_test(ax=ax)

Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

(63,) (63,)
(63,) (63,)
avg_peak 1.6845488102985742
skipped 2 symbols at 10079.0
skipped 2 symbols at 30870.0
skipped 2 symbols at 42209.5
decoding [ref|dec]:
 44| 44 ✔     47| 47 ✔    117|117 ✔     64| 64 ✔     67| 67 ✔    123|123 ✔     67| 67 ✔    103|103 ✔    
  9|  9 ✔     83| 83 ✔     21| 21 ✔    114|114 ✔     36| 36 ✔     87| 87 ✔     70| -1       88| 88 ✔    
 88| 88 ✔     12| 12 ✔     58| 58 ✔     65| 65 ✔    102|102 ✔     39| 39 ✔     87| 87 ✔     46| 46 ✔    
 88| 88 ✔     81| 81 ✔     37| 37 ✔     25| 25 ✔     77| 77 ✔     72| 72 ✔      9|  9 ✔     20| 20 ✔    
115|115 ✔     80| 80 ✔    115|115 ✔     69| 69 ✔    126|126 ✔     79| 79 ✔     47| 47 ✔     64| 64 ✔    
 82| 82 ✔     99| 99 ✔     88| 88 ✔     49| 49 ✔    115|115 ✔     29| 29 ✔     19| 19 ✔     19| -1      
 14| 14 ✔     39| 39 ✔     32| 32 ✔     65| 65 ✔      9|  9 ✔     57| 57 ✔    127|127 ✔     32| 32 ✔    
 31| 31 ✔     74| 74 ✔    116|116 ✔     23| 23 ✔     35| 35 ✔    126|126 ✔     75| 75 ✔    114|114 ✔    
 

In [84]:
sample_duration=128
sample_reps = 25
sweep_points = 25

default_params = dict(
        nbits=6,
        signal_amplitude=2.0e-3,
        decimation=10,
        threshold_factor=4.0,
        power_avg_width=2.5,
        max_lookahead=6.5)

fig, ax = plt.subplots(figsize=(12, 9))

for nbits in [5, 6]: # FIXME make sim stable for higher bit counts
    print(f'nbits={nbits}')
    
    def calculate_ser(v):
        params = dict(default_params)
        params['signal_amplitude'] = v
        params['nbits'] = nbits
        sers, brs = [], []
        for i in range(sample_reps):
            ser, br = run_ser_test(**params, sample_duration=sample_duration, print=noprint, seed=np.random.randint(0xffffffff))
            sers.append(ser)
            brs.append(br)
        sers, brs = np.array(sers), np.array(brs)
        ser = np.mean(sers)
        print(f'signal_amplitude={v:<.5f}: ser={ser:<.5f} ±{np.std(sers):<.5f}, br={np.mean(brs):<.5f}')
        return ser
    
    vs = 0.2e-3 * 10 ** np.linspace(0, 1.0, sweep_points)
    with Pool(6) as p:
        data = p.map(calculate_ser, vs)
    
    ax.plot(vs, data, label=f'{nbits} bit')
ax.grid()
ax.set_xlabel('Amplitude in mHz')
ax.set_ylabel('Symbol error rate')
ax.legend()

<ipython-input-84-f36c7b0ffb61>:13: RuntimeWarning: More than 20 figures have been opened. Figures created through the pyplot interface (`matplotlib.pyplot.figure`) are retained until explicitly closed and may consume too much memory. (To control this warning, see the rcParam `figure.max_open_warning`).
  fig, ax = plt.subplots(figsize=(12, 9))


Canvas(toolbar=Toolbar(toolitems=[('Home', 'Reset original view', 'home', 'home'), ('Back', 'Back to previous …

nbits=5
signal_amplitude=0.00029: ser=1.01000 ±0.012207515615390381, br=-5.62500
signal_amplitude=0.00020: ser=1.01469 ±0.013678792892649557, br=-8.26172
signal_amplitude=0.00052: ser=1.00406 ±0.018895270572288715, br=-2.28516
signal_amplitude=0.00043: ser=1.01000 ±0.018817586521655747, br=-5.62500
signal_amplitude=0.00024: ser=1.01156 ±0.014510233457804875, br=-6.50391
signal_amplitude=0.00036: ser=1.00687 ±0.014875787794264881, br=-3.86719
signal_amplitude=0.00032: ser=1.01156 ±0.01837117307087384, br=-6.50391
signal_amplitude=0.00022: ser=1.01000 ±0.013535254892317322, br=-5.62500
signal_amplitude=0.00057: ser=1.00281 ±0.012476540486048206, br=-1.58203
signal_amplitude=0.00039: ser=1.00812 ±0.014402148277253642, br=-4.57031
signal_amplitude=0.00047: ser=1.00438 ±0.012899854650343935, br=-2.46094
signal_amplitude=0.00027: ser=1.00937 ±0.014657549249448218, br=-5.27344
signal_amplitude=0.00063: ser=0.99938 ±0.019253652250936705, br=0.35156
signal_amplitude=0.00077: ser=0.99156 ±0.0323